# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

In [96]:
!pip install benepar

In [97]:
!pip install tensorflow

# **Question 1**

(40 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of the product [2019 Dell labtop](https://www.amazon.com/Dell-Inspiron-5000-5570-Laptop/dp/B07N49F51N/ref=sr_1_11?crid=1IJ7UWF2F4GHH&keywords=dell%2Bxps%2B15&qid=1580173569&sprefix=dell%2Caps%2C181&sr=8-11&th=1) on amazon.

(2) Collect the top 100 User Reviews of the film [Joker](https://www.imdb.com/title/tt7286456/reviews?ref_=tt_urv) from IMDB.

(3) Collect the abstracts of the top 100 research papers by using the query [natural language processing](https://citeseerx.ist.psu.edu/search?q=natural+language+processing&submit.x=0&submit.y=0&sort=rlv&t=doc) from CiteSeerX.

(4) Collect the top 100 tweets by using hashtag ["#CovidVaccine"](https://twitter.com/hashtag/CovidVaccine) from Twitter. 


In [98]:
import json
import tweepy
import csv
import pandas as pd
import nltk
import benepar
import spacy
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from textblob import Word
from benepar.spacy_plugin import BeneparComponent
from spacy import displacy
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('averaged_perceptron_tagger')
nltk.download('universal_tagset')
nltk.download('wordnet')
benepar.download('benepar_en3')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package universal_tagset to /root/nltk_data...
[nltk_data]   Package universal_tagset is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package benepar_en3 to /root/nltk_data...
[nltk_data]   Package benepar_en3 is already up-to-date!


True

##Collecting 100 CovidVaccine tweets from TWITTER##

In [99]:
twitter_credentials = dict()
twitter_credentials['CONSUMER_KEY'] = 'u7L1lnR7HN85dn1qnTFO1cegb'
twitter_credentials['CONSUMER_SECRET'] = 'QN1JrEmit2To46ZcwWAT4aI5QGWZXWRDDUPnMCWV5M66SFc8wT'
twitter_credentials['ACCESS_KEY'] = '1144377060036620294-BSEicX3zH7hIhksbNZV9mrWFwa07cO'
twitter_credentials['ACCESS_SECRET'] = 'gxWMOodDq1nQAjix9mHEOUSAtgE7XH5ctHInm0XRslJce'
created=[]
tweetext=[]
with open('twitter_credentials.json', 'w') as secret_info:
  json.dump(twitter_credentials, secret_info, indent=4, sort_keys=True)
with open('twitter_credentials.json') as cred_data:
  info = json.load(cred_data)
  key_of_consumer = info['CONSUMER_KEY']
  secrets_of_consumer = info['CONSUMER_SECRET']
  key_for_access = info['ACCESS_KEY']
  secrets_for_access = info['ACCESS_SECRET']
  authentification = tweepy.OAuthHandler(key_of_consumer, secrets_of_consumer)
  api = tweepy.API(authentification )
  extracted_tweets = 100000000 #int(input('No. of tweets to extract- '))
  tag = 'CovidVaccine' #input('Please enter the topics to extract. ')
  for i in tweepy.Cursor(api.search, q='#' + tag, rpp=100).items(extracted_tweets):
    created.append(i.created_at)
    tweetext.append(i.text)
tweets_of_covid = pd.DataFrame({'tweets':tweetext,'created':created})
tweets_of_covid.to_csv('corona_vaccine.csv')
print(tweets_of_covid[:100])

                                               tweets             created
0   RT @ichaydon: A year ago I tried the Moderna v... 2021-04-02 13:50:50
1   RT @ichaydon: A year ago I tried the Moderna v... 2021-04-02 13:50:49
2   Today marks two weeks since I received my seco... 2021-04-02 13:50:45
3   RT @ichaydon: A year ago I tried the Moderna v... 2021-04-02 13:50:39
4   RT @ichaydon: A year ago I tried the Moderna v... 2021-04-02 13:50:39
..                                                ...                 ...
95  👇🏻👏🏻#BrockU #CovidVaccine https://t.co/4pWrdZ5SMb 2021-04-02 13:40:05
96  If you observe #Passover or #Easter and will b... 2021-04-02 13:40:05
97  If you observe #Passover or #Easter and will b... 2021-04-02 13:40:05
98              Here we go.. #CovidVaccine #firstshot 2021-04-02 13:39:55
99  RT @ichaydon: A year ago I tried the Moderna v... 2021-04-02 13:39:50

[100 rows x 2 columns]


# **Question 2**

(30 points). Write a python program to **clean the text data** you collected above and save the data in a new column in the csv file. The data cleaning steps include:



(1) Remove noise, such as special characters and punctuations.

In [100]:
tweets_of_covid['Noise removal']=tweets_of_covid['tweets'].str.replace('[^\w\s]','')
tweets_of_covid['Noise removal']=tweets_of_covid['tweets'].apply(lambda x: " ".join(x for x in x.split()))

(2) Remove numbers.

In [101]:
#Numbers removal
tweets_of_covid['Numbers removal']=tweets_of_covid['Noise removal'].str.replace('[0-9]','')

(3) Remove stopwords by using the [stopwords list](https://gist.github.com/sebleier/554280).

In [102]:
#Stop words removal
stop = stopwords.words('english')
tweets_of_covid['Stopwords removal']=tweets_of_covid['Numbers removal'].apply(lambda x: " ".join(x for x in x.split() if x not in stop))

(4) Lowercase all texts

In [103]:
#Lowercase
tweets_of_covid['lowercase']=tweets_of_covid['Stopwords removal'].apply(lambda x: " ".join(x.lower() for x in x.split()))


(5) Stemming. 


In [104]:
#Stemming
st = PorterStemmer()
tweets_of_covid['stemming']=tweets_of_covid['lowercase'].apply(lambda x: " ".join([st.stem(word) for word in x.split()]))









(6) Lemmatization.

In [105]:
#Lemmatization
tweets_of_covid['after Lemmatization']=tweets_of_covid['stemming'].apply(lambda x: " ".join([Word(word).lemmatize() for word in x.split()]))
tweets_of_covid

tweets  ...                                after Lemmatization
0    RT @ichaydon: A year ago I tried the Moderna v...  ...  rt @ichaydon: a year ago i tri moderna vaccin ...
1    RT @ichaydon: A year ago I tried the Moderna v...  ...  rt @ichaydon: a year ago i tri moderna vaccin ...
2    Today marks two weeks since I received my seco...  ...  today mark two week sinc i receiv second moder...
3    RT @ichaydon: A year ago I tried the Moderna v...  ...  rt @ichaydon: a year ago i tri moderna vaccin ...
4    RT @ichaydon: A year ago I tried the Moderna v...  ...  rt @ichaydon: a year ago i tri moderna vaccin ...
..                                                 ...  ...                                                ...
190  If you’re aged over 50, a carer, or have an un...  ...  if you’r age , carer, underli health condition...
191  RT @pettet50: Interim Estimates of Vaccine Eff...  ...  rt @pettet: interim estim vaccin effect bntb m...
192  RT @WADeptHealth: Exciting news: The #COVIDvac...  ...  rt @wadepthealth: excit news: the #covidvaccin...
193  RT @PanagiotisMylo6: Γάλλος Υπουργός Υγείας Ol...  ...  rt @panagiotismylo: γάλλος υπουργός υγείας oli...
194  RT @surgeon_sheel07: कोविड-१९ लसीकरण - समज/गैर...  ...  rt @surgeon_sheel: कोविड-१९ लसीकरण - समज/गैरसम...

[195 rows x 8 columns]

# **Question 3**

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes: 

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.




In [106]:
partsofspeech=[]
c=[]
n=0
for i in tweets_of_covid['tweets']:
  partsofspeech.append(nltk.pos_tag(nltk.word_tokenize(i),tagset='universal'))
  c.append(nltk.FreqDist(tag for (word, tag) in partsofspeech[0]))
  print(partsofspeech[n])
  print(c[n])
  n=n+1
print(c)

[('RT', 'NOUN'), ('@', 'NOUN'), ('ichaydon', 'NOUN'), (':', '.'), ('A', 'DET'), ('year', 'NOUN'), ('ago', 'ADV'), ('I', 'PRON'), ('tried', 'VERB'), ('the', 'DET'), ('Moderna', 'NOUN'), ('vaccine', 'NOUN'), ('to', 'PRT'), ('see', 'VERB'), ('if', 'ADP'), ('it', 'PRON'), ('was', 'VERB'), ('safe', 'ADJ'), ('.', '.'), ('(', '.'), ('Spoiler', 'NOUN'), (':', '.'), ('It', 'PRON'), ('is', 'VERB'), ('!', '.'), (')', '.'), ('Now', 'ADV'), (',', '.'), ('on', 'ADP'), ('my', 'PRON'), ('#', '.'), ('COVIDvaccine', 'NOUN'), ('anniversary', 'NOUN'), (',', '.'), ('I', 'PRON'), ('’', 'VERB'), ('m', 'ADJ'), ('hap…', 'NOUN')]
<FreqDist with 9 samples and 38 outcomes>
[('RT', 'NOUN'), ('@', 'NOUN'), ('ichaydon', 'NOUN'), (':', '.'), ('A', 'DET'), ('year', 'NOUN'), ('ago', 'ADV'), ('I', 'PRON'), ('tried', 'VERB'), ('the', 'DET'), ('Moderna', 'NOUN'), ('vaccine', 'NOUN'), ('to', 'PRT'), ('see', 'VERB'), ('if', 'ADP'), ('it', 'PRON'), ('was', 'VERB'), ('safe', 'ADJ'), ('.', '.'), ('(', '.'), ('Spoiler', 'NOUN')

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

In [107]:
# Dependcy parsing
h=spacy.load('en_core_web_sm')
for j in tweets_of_covid['tweets']:
  displacy.render(h(j),jupyter=True)
# constituent parsing
%tensorflow_version 1.x
model= spacy.load('en')
model.add_pipe(BeneparComponent('benepar_en3'))
for i in tweets_of_covid['tweets']:
  print(list(model(i).sents)[0]._.parse_string)

/usr/local/lib/python3.7/dist-packages/torch/distributions/distribution.py:46: UserWarning: <class 'torch_struct.distributions.TreeCRF'> does not define `arg_constraints`. Please set `arg_constraints = {}` or initialize the distribution with `validate_args=False` to turn off validation.
  'with `validate_args=False` to turn off validation.')


(NP (NNP RT) (NNP @ichaydon) (: :))
(NP (NNP RT) (NNP @ichaydon) (: :))
(S (NP (NN Today)) (VP (VBZ marks) (NP (NP (CD two) (NNS weeks)) (SBAR (IN since) (S (NP (PRP I)) (VP (VBD received) (NP (PRP$ my) (JJ second) (NNP Moderna) (NN vaccine))))))) (. !))
(NP (NNP RT) (NNP @ichaydon) (: :))
(NP (NNP RT) (NNP @ichaydon) (: :))
(NP (NNP RT) (NNP @ichaydon) (: :))
(NP (NP (ADJP (RB Really) (JJ good)) (NN advice)) (ADVP (RB here)) (. .))
(NP (NNP RT) (NNP @ichaydon) (: :))
(NP (NNP RT) (NNP @WADeptHealth) (: :))
(NP (NP (NNP RT) (NNP @drharshvardhan)) (: :) (NP (`` #) (CD COVID19) (-LRB- संक्रमण) (-RRB- से) (FW लोगों) (-RRB- को)))
(NP (NNP RT) (NNP @ichaydon) (: :))
(NP (NNP RT) (NNP @ichaydon) (: :))
(S (NP (NP (DT The) (NN price)) (PP (IN of) (NP ($ #) (NNP COVIDVaccine)))) (VP (VBZ has) (VP (VBN been) (VP (VBN capped) (PP (IN at) (NP (NP ($ Rs) (CD 250)) (PP (IN per) (NP (NN dose))))) (PP (IN in) (NP (NP (JJ private) (NNS hospitals)) (PP (IN across) (NP (NNP India)))))))) (. .) (_SP 

))


(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

In [108]:
t=[]
l = spacy.load('en_core_web_sm')
for i in tweets_of_covid['tweets']:
  for j in l(i).ents:
    t.append((j.label_,j.text))
    print(j.label_,j.text)
nltk.FreqDist(label for (label, text) in t)

DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE Today
DATE two weeks
ORDINAL second
PERSON Moderna
PERCENT 100%
PERSON VACCINATED
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
CARDINAL 16
CARDINAL 2
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
PERSON COVIDVaccine
CARDINAL 250
GPE India
PERSON CoronavirusIndia
MONEY #Maharashtra #MP #UttarPradesh
PERCENT 82%
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
DATE A year ago
GPE Moderna
MONEY #COVIDvaccine anniversary
PERSON VaxFact
MONEY #covid19 #
CARDINAL millions
GPE India
ORDINAL second
PERSON TNIE
MONEY LargestVaccineDrive
P

FreqDist({'CARDINAL': 51,
          'DATE': 73,
          'EVENT': 1,
          'FAC': 2,
          'GPE': 70,
          'LOC': 4,
          'MONEY': 113,
          'NORP': 8,
          'ORDINAL': 18,
          'ORG': 72,
          'PERCENT': 3,
          'PERSON': 100,
          'PRODUCT': 8,
          'WORK_OF_ART': 1})

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):** 


###Constituency parsing tree###

Constituency parsing is analysing the sub phrases by breaking the sentence. These sub phrases are also known as constituents. The constituents are categorized into different categories of grammar like Noun and Verb phrase.

Constituency parsing aims to extract a constituency-based parse tree from a sentence that represents its syntactic structure according to a phrase structure grammar.

For example, the phrases "a cat", "a dog", "a computer " are all Noun phrases, where as "eat a chicken" " go to school" are all verb phrases

###Dependency parsing tree###
Dependency parsing is opposite to constituency parsing, dependency parsing doesnot make use of constituents or sub-phrases.
Depndency parse tree first divides all words in a sentence and furthur establishes the reationship between the words for the better syntactic understanding.
Dependency parsing considers each word as a node. In this parsing each word is connected based on their relationships. 